- Copyright 2021. Dongwon Kim All rights reserved.
- File name : ImageCaptioning.ipynb
- Written by Dongwon Kim
- Image Captioning
    - build a ImageCaptioning model for flickr-8k
- Modificatoin history
    - written by Dongwon Kim on Oct 25, 2021

In [ ]:
import os

import numpy as np
import json
import torch
import torchvision.transforms as transforms
from torch.utils.data import Dataset, DataLoader, sampler
import torch.nn as nn
from torchvision.models import resnet101
from torch.nn.utils.rnn import pack_padded_sequence
import matplotlib.pyplot as plt
import string

from multiprocessing import cpu_count
from collections import Counter
from PIL import Image

from google.colab import files

# Get data
- need to install kaggle and upload own kaggle.json file
```
$pip install kaggle
```
- Download dataset
- Unzip data

In [ ]:
!kaggle datasets download -d kunalgupta2616/flickr-8k-images-with-captions

 99% 1.02G/1.04G [00:07<00:00, 157MB/s]
100% 1.04G/1.04G [00:07<00:00, 147MB/s]


In [ ]:
!unzip flickr-8k-images-with-captions.zip

스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.
  inflating: Images/2844846111_8c1cbfc75d.jpg  
  inflating: Images/2844963839_ff09cdb81f.jpg  
  inflating: Images/2845246160_d0d1bbd6f0.jpg  
  inflating: Images/2845691057_d4ab89d889.jpg  
  inflating: Images/2845845721_d0bc113ff7.jpg  
  inflating: Images/2846037553_1a1de50709.jpg  
  inflating: Images/2846785268_904c5fcf9f.jpg  
  inflating: Images/2846843520_b0e6211478.jpg  
  inflating: Images/2847514745_9a35493023.jpg  
  inflating: Images/2847615962_c330bded6e.jpg  
  inflating: Images/2847859796_4d9cb0d31f.jpg  
  inflating: Images/2848266893_9693c66275.jpg  
  inflating: Images/2848571082_26454cb981.jpg  
  inflating: Images/2848895544_6d06210e9d.jpg  
  inflating: Images/2848977044_446a31d86e.jpg  
  inflating: Images/2849194983_2968c72832.jpg  
  inflating: Images/2850719435_221f15e951.jpg  
  inflating: Images/2851198725_37b6027625.jpg  
  inflating: Images/2851304910_b5721199bc.jpg  
  inflating: Images/2851931813_eaf8ed7be3.jpg  
  in

- unzipped images are stoed in Images folder
- captions.txt
    - img name, caption per line
    - 5 captions for a img
    → 5 same img name for different captions
- reference: [kaggle](https://www.kaggle.com/kunalgupta2616/flickr-8k-images-with-captions)

In [ ]:
!ls

captions.txt  flickr-8k-images-with-captions.zip  Images  sample_data


# Reference
1. **N. Habbash, “Image Captioning: a Show and Tell implementation,” University of Milano-Bicocca**
    - for model, batch size, learning rate etc are refered from the paper
2. **Week8_01_ImageCaptioning_1021.ipynb**
    - for Vocabulary, Enoder and Decoder, also referenced the given code for the class material.

# Preprocessing

## Resize image
- since size of images(in *image_dir*) are different, resize the image to *size* 
- store resized iamge to *output_dir*
---
- in this code, resize to (256, 256)

In [ ]:
def resize_images(image_dir, output_dir, size):
    if not os.path.exists(output_dir):
        os.makedirs(output_dir)

    images = os.listdir(image_dir)
    num_images = len(images)

    for i, image in enumerate(images):
        with open(os.path.join(image_dir, image), 'r+b') as f:
            with Image.open(f) as img:
                img = img.resize(size, Image.ANTIALIAS)
                img.save(os.path.join(output_dir, image), img.format)
        if(i + 1) % 10000 == 0:
            print("[{}/{}] Image Resized".format(i + 1, num_images))

In [ ]:
image_dir = './Images'
output_dir = './data/resized'
image_size = [256, 256]

resize_images(image_dir, output_dir, image_size)

## Vocabulary
- build vocabulary for captions

### read_file
- get json file for vocab if exists
- if not, make json file for vocab

    ```json
        {
            'word2idx': ,
            'idx2word': ,
            'word_cnt': 
        }
    ```

### build_vocab
- caption_mapped:
    - dict that have img name(without '.jpg') for key and array of captions for value
    - captions are cleaned(lower, remove things except alphabet)
- for each img, captions pair
    - count freq of word
    - add word to vocab if the freq exceed threshold

### add_word
- add word to vocab
    - if word is not in vocab, add word to word2idx and idx2word




In [ ]:
class Vocabulary(object):
    def __init__(self, threshold, vocab_file, caption_mapped):
        self.threshold = threshold
        self.vocab_file = vocab_file
        self.caption_mapped = caption_mapped

        self.word2idx = {}
        self.idx2word = []
        self.idx = 0
        self.word_cnt = Counter()

        self.read_file()

    def add_word(self, word):
        if not word in self.word2idx:
            self.word2idx[word] = self.idx
            self.idx2word.append(word)
            self.idx += 1
    
    def read_file(self):
        if(os.path.exists(self.vocab_file)):
            with open(self.vocab_file, 'r') as f:
                vocab = json.load(f)
                self.word2idx = vocab['word2idx']
                self.idx2word = vocab['idx2word']
                self.idx = len(self.idx2word) + 1
                self.word_cnt = Counter(vocab['word_cnt'])
        else:
            self.build_vocab()
            with open(self.vocab_file, 'w', encoding = 'utf-8') as f:
                json.dump({
                    'word2idx': self.word2idx,
                    "idx2word": self.idx2word,
                    "word_cnt": self.word_cnt
                }, f)

    def build_vocab(self):
        for _, captions in caption_mapped.items():
             for i in range(len(captions)):
                    self.word_cnt.update(captions[i].split())

        words = [word for word, cnt in self.word_cnt.items() if cnt >= self.threshold]

        self.add_word('<pad>')
        self.add_word('<start>')
        self.add_word('<end>')
        self.add_word('<unk>')

        for w in words:
            self.add_word(w)

    def __call__(self, word):
        if not word in self.word2idx:
            return self.word2idx['<unk>']
        return self.word2idx[word]

    def __len__(self):
        return len(self.word2idx)


## Tokenize
- read captions.txt comes from the dataset
- for each line(split it in each line)
    - get img name and caption(split the line with ',')
        - get img name without file extension
        - make dictionary 
            - key: img name
            - value: captions(5 captions are stored as array)
- for completed dictionary
    - do cleaning
- store the result in *output_file* as json file

In [ ]:
def tokenize(input_file, output_file):
    f = open(input_file, 'r')
    f.readline()
    text = f.read()
    f.close()
    
    explain=dict()
    for line in text.split('\n'):
        tokens = line.split(',')
        if(len(line) > 2):
            id = tokens[0].split('.')[0] # img name
            desc = ' '.join(tokens[1:]) # descriptions
            if id not in explain:
               explain[id] = list()
            explain[id].append(desc)
            #explain.append([id, desc])
    cleaning(explain)
    
 
    with open(output_file, 'w', encoding="utf-8", ) as f:
        json.dump(explain, f)
    return explain

## Cleaning
- for captions in dictionary
    - get each word(split by ' ')
    - change the word to lower case, remove punctuation marks
    - store only if the length of word is greater than 1 and alphabet
    - make sentence again with transformed word(by  ' '.join)

In [ ]:
def cleaning(explain):
    remove = str.maketrans('', '', string.punctuation)
    for key, descs in explain.items():
        for i in range(len(descs)):
            desc = descs[i]
            desc = desc.split()
            desc = [word.lower() for word in desc]
            desc = [word.translate(remove) for word in desc]
            desc = [word for word in desc if len(word) > 1]
            desc = [word for word in desc if word.isalpha()]
            descs[i] = ' '.join(desc)
        
        
            

In [ ]:
caption_mapped = tokenize('./captions.txt', './data/caption.json')

mapped and cleand captions

In [ ]:
caption_mapped

{'1000268201_693b08cb0e': ['child in pink dress is climbing up set of stairs in an entry way',
  'girl going into wooden building',
  'little girl climbing into wooden playhouse',
  'little girl climbing the stairs to her playhouse',
  'little girl in pink dress going into wooden cabin'],
 '1001773457_577c3a7d70': ['black dog and spotted dog are fighting',
  'black dog and tricolored dog playing with each other on the road',
  'black dog and white dog with brown spots are staring at each other in the street',
  'two dogs of different breeds looking at each other on the road',
  'two dogs on pavement moving toward each other'],
 '1002674143_1b742ab4b8': ['little girl covered in paint sits in front of painted rainbow with her hands in bowl',
  'little girl is sitting in front of large painted rainbow',
  'small girl in the grass plays with fingerpaints in front of white canvas with rainbow on it',
  'there is girl with pigtails sitting in front of rainbow painting',
  'young girl with pi

In [ ]:
ll = [ele for ele in caption_mapped]
print(ll)

['1000268201_693b08cb0e', '1001773457_577c3a7d70', '1002674143_1b742ab4b8', '1003163366_44323f5815', '1007129816_e794419615', '1007320043_627395c3d8', '1009434119_febe49276a', '1012212859_01547e3f17', '1015118661_980735411b', '1015584366_dfcec3c85a', '101654506_8eb26cfb60', '101669240_b2d3e7f17b', '1016887272_03199f49c4', '1019077836_6fc9b15408', '1019604187_d087bf9a5f', '1020651753_06077ec457', '1022454332_6af2c1449a', '1022454428_b6b660a67b', '1022975728_75515238d8', '102351840_323e3de834', '1024138940_f1fefbdce1', '102455176_5f8ead62d5', '1026685415_0431cbf574', '1028205764_7e8df9a2ea', '1030985833_b0902ea560', '103106960_e8a41d64f8', '103195344_5d2dc613a3', '103205630_682ca7285b', '1032122270_ea6f0beedb', '1032460886_4a598ed535', '1034276567_49bb87c51c', '104136873_5b5d41be75', '1042020065_fb3d3ba5ba', '1042590306_95dea0916c', '1045521051_108ebc19be', '1048710776_bb5b0a5c7c', '1052358063_eae6744153', '105342180_4d4a40b47f', '1053804096_ad278b25f1', '1055623002_8195a43714', '1055753

In [ ]:
caption_mapped['1000268201_693b08cb0e']

['child in pink dress is climbing up set of stairs in an entry way',
 'girl going into wooden building',
 'little girl climbing into wooden playhouse',
 'little girl climbing the stairs to her playhouse',
 'little girl in pink dress going into wooden cabin']

## Dataset
- make dictionary for captions
- for each img and captions for index given as input,
    - open and transform img
    - for each caption
        - tokenize the caption and get index for the token from vocab 
        - mark start and end for caption
        - padd the caption with 0(='pad') for the max length in total captions 
    - return img and caption when getitem

- random_choice
    - return randomly chosen index

In [ ]:
class FlickrDS(Dataset):
    def __init__(self, batch_size, threshold, vocab_file, caption_mapped, transform=None):
        self.vocab = Vocabulary(threshold = threshold, vocab_file = vocab_file, caption_mapped = caption_mapped)
        self.batch_size = batch_size
        self.transform = transform

        for _, captions in caption_mapped.items():
            self.cap_length = [len(caption.split()) for caption in captions]
        self.captions_ids = [ele for ele in caption_mapped]

    def __getitem__(self, index):
        img_id = self.captions_ids[index]
        captions = caption_mapped[img_id]

        path = './Images/' + img_id + '.jpg'
        img = Image.open(path).convert('RGB')

        if self.transform is not None:
            img = self.transform(img)

        
     
        for i, (caption) in enumerate(captions):
            tokens = caption.split()   
            encoded=[]         
            encoded.append(self.vocab('<start>'))
            encoded.extend([self.vocab(token) for token in tokens])
            encoded.append(self.vocab('<end>'))    
            encoded = encoded + [0] * (max(self.cap_length) + 2 - len(encoded))            
            encoded = torch.Tensor(encoded).long()      
        return img, encoded

    
    def rand_choice(self):
        sel_length = np.random.choice(self.cap_length)
        index = np.where(self.cap_length == sel_length)[0]
        index = list(np.random.choice(index, size = self.batch_size))
        return index

    def __len__(self):
        return len(self.captions)




- transform img

In [ ]:
transform = transforms.Compose([
    transforms.RandomCrop(224),
    transforms.RandomHorizontalFlip(),
    transforms.ToTensor(),
    transforms.Normalize((0.485, 0.456, 0.406), (0.299, 0.224, 0.225))
])

- get dataset

In [ ]:
train_dataset = FlickrDS(batch_size = 32, threshold=4, vocab_file = './data/vocab.json', caption_mapped=caption_mapped, transform = transform)

## Set dataloader
- shuffle and split the data in batch size

In [ ]:
indices = train_dataset.rand_choice()
train_sampler = sampler.SubsetRandomSampler(indices=indices)
length_sampler = sampler.BatchSampler(sampler=train_sampler, batch_size=32, drop_last=False)
train_loader = DataLoader(train_dataset, batch_sampler=length_sampler)

# Model

## Encoder
- use pretrained resnet101 as mentioned in the referencing paper
- remove the last layer FC layer for making latent vector
- add intermediate FC layer

In [ ]:
class Encoder(nn.Module):
    def __init__(self):
        super().__init__()
        pretrained = resnet101(pretrained = True)
        layers = list(pretrained.children())[:-1]
        self.resnet = nn.Sequential(*layers)
        self.linear = nn.Linear(pretrained.fc.in_features, 512)
        self.bn = nn.BatchNorm1d(512, momentum=0.01)
    
    def forward(self, x):
        with torch.no_grad():
            features = self.resnet(x)
        features = features.view(features.size(0), -1)
        latent_vector = self.bn(self.linear(features))
        return latent_vector


## Decoder
- use LSTM for decoder(referencing the paper)
- for output layer, add Dense layer

In [ ]:
class Decoder(nn.Module):
    def __init__(self, vocab_size):
        super().__init__()
        self.embed = nn.Embedding(vocab_size, 512)
        
        self.lstm = nn.LSTM(512, 512, 1, batch_first=True)    # Single layer LSTM
        self.linear = nn.Linear(512, vocab_size)
        
    def forward(self, features, captions):
        captions = captions[:, :-1]
        embeddings = self.embed(captions)
        embeddings = torch.cat((features.unsqueeze(1), embeddings), 1)
        
        hiddens, _ = self.lstm(embeddings)
        outputs = self.linear(hiddens)
        return outputs

## ImgCaption
- using the encoder and decoder, make image captioning model

In [ ]:
class ImgCaption(nn.Module):
    def __init__(self, encoder, decoder):
        super().__init__()
        self.encoder = encoder
        self.decoder = decoder

    def forward(self, img, caps):
        features = encoder(img)
        outputs = decoder(features, caps)

        return outputs


# Train

## Setting
- find gpu
- set model, loss function and optimizer
- in optimizer, optimize parameters except pretrained resnet101's

In [ ]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

encoder = Encoder().to(device)
decoder = Decoder(len(train_dataset.vocab)).to(device)
model = ImgCaption(encoder, decoder)
model = model.to(device)

criterion = nn.CrossEntropyLoss()
params = list(decoder.parameters()) + list(encoder.linear.parameters()) + list(encoder.bn.parameters())
optimizer = torch.optim.Adam(params, lr=0.001)

## Train the model
- Although the paper runs for 10 epochs, comparing the loss for 10, 20, 30, run for 20 epochs
- store the model

In [ ]:
EPOCHS = 20

total_step = len(train_loader)

encoder.train()
decoder.train()

for epoch in range(EPOCHS):
    indices = train_loader.dataset.rand_choice()
    length_sampler = sampler.SubsetRandomSampler(indices=indices)
    train_loader.batch_sampler.sampler = length_sampler
   
    for i, (img, caps) in enumerate(train_loader):
   
        img = img.to(device)
        caps = caps.to(device)
        lengths = [len(cap) for cap in caps]
        targets = pack_padded_sequence(caps, lengths, batch_first=True)[0]
        outputs = model(img, caps)


        loss = criterion(outputs.view(-1, len(train_loader.dataset.vocab)), targets.view(-1))
        loss.backward()
        optimizer.step() 
        

   
    print('Epoch [{}/{}], Step [{}/{}], Loss: {:.4f}'.format(epoch + 1, EPOCHS, i + 1, total_step, loss.item()))

torch.save(model.state_dict(), './2018312292_DongwonKim.pt')


Epoch [1/20], Step [1/1], Loss: 8.1354
Epoch [2/20], Step [1/1], Loss: 8.0751
Epoch [3/20], Step [1/1], Loss: 8.1097
Epoch [4/20], Step [1/1], Loss: 7.9976
Epoch [5/20], Step [1/1], Loss: 7.8294
Epoch [6/20], Step [1/1], Loss: 7.5689
Epoch [7/20], Step [1/1], Loss: 7.5467
Epoch [8/20], Step [1/1], Loss: 6.0977
Epoch [9/20], Step [1/1], Loss: 5.6142
Epoch [10/20], Step [1/1], Loss: 5.0752
Epoch [11/20], Step [1/1], Loss: 4.4056
Epoch [12/20], Step [1/1], Loss: 5.2959
Epoch [13/20], Step [1/1], Loss: 3.8190
Epoch [14/20], Step [1/1], Loss: 3.9495
Epoch [15/20], Step [1/1], Loss: 3.8497
Epoch [16/20], Step [1/1], Loss: 5.1006
Epoch [17/20], Step [1/1], Loss: 4.4889
Epoch [18/20], Step [1/1], Loss: 4.4844
Epoch [19/20], Step [1/1], Loss: 4.7721
Epoch [20/20], Step [1/1], Loss: 4.5570


# Test

- load and transform images for testing(given from the assignment)

In [ ]:
def load_img(img):
    img_path = os.path.join('./data/test_images/', img)
    img = Image.open(img_path).convert('RGB')
    img = img.resize([224, 224], Image.LANCZOS)
    transform = transforms.Compose([
        transforms.ToTensor(),
        transforms.Normalize((0.485, 0.456, 0.406), (0.229, 0.224, 0.225))
    ])
    img = transform(img).unsqueeze(0)
    return img
    
    return img

In [ ]:
!cd ./data/test_images

In [ ]:
!ls ./data/test_images

randomimage0.jpg  randomimage3.jpg  randomimage6.jpg  randomimage9.jpg
randomimage1.jpg  randomimage4.jpg  randomimage7.jpg
randomimage2.jpg  randomimage5.jpg  randomimage8.jpg


## load the model

In [ ]:
new_model = ImgCaption(encoder, decoder)
new_model.load_state_dict(torch.load('./ImageCaptioning.pt'))
new_model = new_model.to(device)

new_encoder = new_model.encoder
new_decoder = new_model.decoder

## Testing

In [ ]:
img_path = './data/test_images/'
images = os.listdir(img_path)
print(images)
max_seq_length = 20
captions=[]
for img in images:
    if(img == '.ipynb_checkpoints'):
        continue
    transfered_img = load_img(img)

    new_encoder.eval()
    new_decoder.eval()    

    word_ids= []

    with torch.no_grad():
        inputs = encoder(transfered_img).unsqueeze(1)
        states = None

        for i in range(max_seq_length):
            hiddens, states = new_model.decoder.lstm(inputs, states)
            outputs = new_model.decoder.linear(hiddens.squeeze(1))
            _, predicted = outputs.max(1)
            word_ids.append(predicted)
            inputs = new_model.decoder.embed(predicted).unsqueeze(1)
        
        word_ids = torch.stack(word_ids, 1)
        word_ids = word_ids[0].detach().cpu().numpy()
    
    caption = []
   
    for id in word_ids:
        word = train_dataset.vocab.idx2word[str(id)]
        if word == '<pad>':
            continue
        caption.append(word)
        if word == '<end>':
            break
    caption = ' '.join(caption)
    captions.append(caption)

['randomimage2.jpg', 'randomimage7.jpg', 'randomimage5.jpg', 'randomimage0.jpg', 'randomimage1.jpg', 'randomimage3.jpg', '.ipynb_checkpoints', 'randomimage6.jpg', 'randomimage4.jpg', 'randomimage9.jpg', 'randomimage8.jpg']


In [ ]:
 images.remove('.ipynb_checkpoints')

## show the result
- the result is printed in sequenc
- by checking the result, find out that they are described well in printed order by chance
> although know that using BLEU to scoring the result is proper, because of lack of time, cannot implement it.

In [ ]:
rows = len(images)
cols = 1
fig = plt.figure(figsize=(100, 100))

for i, img in enumerate(images):

    print(captions[i])
    this_path = os.path.join('./data/test_images/', img)
    this_img = Image.open(this_path)
    ax = fig.add_subplot(rows, cols, i+1)
    ax.imshow(np.asarray(this_img))
    ax.set_title(captions[i])


plt.show()

beret scarves parasailing mountain checkered dish boston checkered clears throwing rough screaming turning bite jeeps lining waterskiing int man <start>
beret scarves parasailing mountain checkered dish boston checkered clears throwing turning father native lining speaks wielding glacier match emerges glacier
display gift dogs <start> <start> <start> <start> <start> <start> <start> <start> <start> <start> <start> <start> <start> <start> <start> <start> <start>
wood jogs focus hugged beam beam beam beam tops device folded watch racer racer star acrobatic match casts match tennis
swing shrine alongside sheltie int sheets diver toboggan sheltie int sheets toboggan corn folded punching folded punching folded punching folded
wood peach houses hikes int sheets toboggan sheltie caution parasailing line folded bin columns folded bin columns folded bin columns
wood cage threewheeled jesus racer sheltie int duck alongside int duck alongside int duck alongside native sheltie int sheets toboggan
w